In [1]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import folium

import warnings
warnings.filterwarnings('ignore')

/opt/anaconda3/lib/python3.8/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  warnings.warn(


In [2]:
gis_df = gpd.read_file('gis_data/CA_block_2010.shp')
gis_df.head()

STATEFP10 COUNTYFP10 TRACTCE10 BLOCKCE10          GEOID10      NAME10  \
0        06        083    980100      1030  060839801001030  Block 1030   
1        06        083    980100      1047  060839801001047  Block 1047   
2        06        083    980100      1029  060839801001029  Block 1029   
3        06        083    980100      1056  060839801001056  Block 1056   
4        06        083    980100      1021  060839801001021  Block 1021   

  MTFCC10 UR10 UACE10 UATYP10 FUNCSTAT10    ALAND10  AWATER10   INTPTLAT10  \
0   G5040    R   None    None          S     167769         0  +34.0591019   
1   G5040    R   None    None          S  132853658      1257  +33.9746147   
2   G5040    R   None    None          S      12286         0  +34.0406847   
3   G5040    R   None    None          S       4986         0  +34.0280957   
4   G5040    R   None    None          S        455         0  +34.0291854   

     INTPTLON10             GISJOIN    Shape_area     Shape_len  \
0  -120.3358673  G06008309801001030  1.677695e+05   3353.624565   
1  -120.1477892  G06008309801001047  1.329158e+08  74313.354262   
2  -120.4588267  G06008309801001029  1.228553e+04    541.743249   
3  -120.4437615  G06008309801001056  4.985548e+03    349.108823   
4  -120.4598499  G06008309801001021  4.548543e+02     87.909874   

                                            geometry  
0  MULTIPOLYGON (((-2206015.932 -101657.724, -220...  
1  POLYGON ((-2181405.165 -113455.943, -2181407.1...  
2  POLYGON ((-2216942.218 -100327.983, -2216930.8...  
3  MULTIPOLYGON (((-2215789.478 -102240.909, -221...  
4  POLYGON ((-2217294.630 -101627.956, -2217296.2...

In [3]:
# We now convert GEOID10 to BLOCK ID to later merge in EJ Screen Data
# Following census.gov's framework, we do so by slicing off the 3 last digit of the GEOID10 column.
gis_df['BLOCKID'] = gis_df['GEOID10'].str.slice(1,12)
gis_df.head()

STATEFP10 COUNTYFP10 TRACTCE10 BLOCKCE10          GEOID10      NAME10  \
0        06        083    980100      1030  060839801001030  Block 1030   
1        06        083    980100      1047  060839801001047  Block 1047   
2        06        083    980100      1029  060839801001029  Block 1029   
3        06        083    980100      1056  060839801001056  Block 1056   
4        06        083    980100      1021  060839801001021  Block 1021   

  MTFCC10 UR10 UACE10 UATYP10 FUNCSTAT10    ALAND10  AWATER10   INTPTLAT10  \
0   G5040    R   None    None          S     167769         0  +34.0591019   
1   G5040    R   None    None          S  132853658      1257  +33.9746147   
2   G5040    R   None    None          S      12286         0  +34.0406847   
3   G5040    R   None    None          S       4986         0  +34.0280957   
4   G5040    R   None    None          S        455         0  +34.0291854   

     INTPTLON10             GISJOIN    Shape_area     Shape_len  \
0  -120.3358673  G06008309801001030  1.677695e+05   3353.624565   
1  -120.1477892  G06008309801001047  1.329158e+08  74313.354262   
2  -120.4588267  G06008309801001029  1.228553e+04    541.743249   
3  -120.4437615  G06008309801001056  4.985548e+03    349.108823   
4  -120.4598499  G06008309801001021  4.548543e+02     87.909874   

                                            geometry      BLOCKID  
0  MULTIPOLYGON (((-2206015.932 -101657.724, -220...  60839801001  
1  POLYGON ((-2181405.165 -113455.943, -2181407.1...  60839801001  
2  POLYGON ((-2216942.218 -100327.983, -2216930.8...  60839801001  
3  MULTIPOLYGON (((-2215789.478 -102240.909, -221...  60839801001  
4  POLYGON ((-2217294.630 -101627.956, -2217296.2...  60839801001

In [5]:
gsw_df = pd.read_csv('gis_data/bay_area_gsw_car.csv')
gsw_df.head()

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0           1  G06000104011003013           0        0        0         0   
1           2  G06000104011003017         162       60       32         0   
2           3  G06000104011003018           4        0        4         0   
3           4  G06000104011003019           0        0        0         0   
4           5  G06000104013001000           0        0        0         0   

   AsianNH  PacIsl  OtherNH  HispLat  ...  samplingTime_NO2  visits_NO2  \
0        0       0        0        0  ...              2686         123   
1       20       1        0       49  ...              8857         400   
2        0       0        0        0  ...               883          85   
3        0       0        0        0  ...              1554         128   
4        0       0        0        0  ...               354          15   

   uniqueDays_NO2  samplingTime_BC  visits_BC  uniqueDays_BC  \
0              42             2614        130             42   
1              72             9019        411             73   
2              45              831         81             45   
3              48             1408        116             45   
4              12              377         18             15   

   samplingTime_UFP  visits_UFP  uniqueDays_UFP      Neighborhood  
0              2340          95              28  Downtown Oakland  
1              7779         346              53  Downtown Oakland  
2               724          71              35  Downtown Oakland  
3               841          63              28  Downtown Oakland  
4               339          14              13  Downtown Oakland  

[5 rows x 28 columns]

In [6]:
gis_df = gis_df.loc[:, ['GISJOIN', 'BLOCKID','INTPTLAT10', 'INTPTLON10','geometry']]
gis_df.columns = ['GISJOIN', 'BLOCKID','lat', 'lon', 'geometry']
gis_df.head()

GISJOIN      BLOCKID          lat           lon  \
0  G06008309801001030  60839801001  +34.0591019  -120.3358673   
1  G06008309801001047  60839801001  +33.9746147  -120.1477892   
2  G06008309801001029  60839801001  +34.0406847  -120.4588267   
3  G06008309801001056  60839801001  +34.0280957  -120.4437615   
4  G06008309801001021  60839801001  +34.0291854  -120.4598499   

                                            geometry  
0  MULTIPOLYGON (((-2206015.932 -101657.724, -220...  
1  POLYGON ((-2181405.165 -113455.943, -2181407.1...  
2  POLYGON ((-2216942.218 -100327.983, -2216930.8...  
3  MULTIPOLYGON (((-2215789.478 -102240.909, -221...  
4  POLYGON ((-2217294.630 -101627.956, -2217296.2...

In [21]:
len(gis_df['GISJOIN'].unique())

708078

In [7]:
gsw_df_merged = gsw_df.merge(gis_df, on='GISJOIN')
gsw_df_merged['BLOCKID'] = gsw_df_merged['BLOCKID'].astype(int)
gsw_df_merged.head()

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0           1  G06000104011003013           0        0        0         0   
1           2  G06000104011003017         162       60       32         0   
2           3  G06000104011003018           4        0        4         0   
3           4  G06000104011003019           0        0        0         0   
4           5  G06000104013001000           0        0        0         0   

   AsianNH  PacIsl  OtherNH  HispLat  ...  visits_BC  uniqueDays_BC  \
0        0       0        0        0  ...        130             42   
1       20       1        0       49  ...        411             73   
2        0       0        0        0  ...         81             45   
3        0       0        0        0  ...        116             45   
4        0       0        0        0  ...         18             15   

   samplingTime_UFP  visits_UFP  uniqueDays_UFP      Neighborhood  \
0              2340          95              28  Downtown Oakland   
1              7779         346              53  Downtown Oakland   
2               724          71              35  Downtown Oakland   
3               841          63              28  Downtown Oakland   
4               339          14              13  Downtown Oakland   

       BLOCKID          lat           lon  \
0  60014011003  +37.8249710  -122.2656150   
1  60014011003  +37.8238070  -122.2637676   
2  60014011003  +37.8241874  -122.2658233   
3  60014011003  +37.8236448  -122.2646514   
4  60014013001  +37.8222391  -122.2610172   

                                            geometry  
0  POLYGON ((-2260969.962 350913.262, -2261011.75...  
1  POLYGON ((-2260735.425 350660.809, -2260737.19...  
2  POLYGON ((-2261011.753 350833.663, -2261038.20...  
3  POLYGON ((-2260863.794 350639.898, -2260903.75...  
4  POLYGON ((-2260690.230 350529.046, -2260672.78...  

[5 rows x 32 columns]

In [19]:
gsw_df_merged

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0              1  G06000104011003013           0        0        0         0   
1              2  G06000104011003017         162       60       32         0   
2              3  G06000104011003018           4        0        4         0   
3              4  G06000104011003019           0        0        0         0   
4              5  G06000104013001000           0        0        0         0   
...          ...                 ...         ...      ...      ...       ...   
6431        6432  G06008106054005013           0        0        0         0   
6432        6433  G06008106135012005           0        0        0         0   
6433        6434  G06008106135012012           0        0        0         0   
6434        6435  G06008106135012014           0        0        0         0   
6435        6436  G06008106135012015           0        0        0         0   

      AsianNH  PacIsl  OtherNH  HispLat  ...  visits_BC  uniqueDays_BC  \
0           0       0        0        0  ...        130             42   
1          20       1        0       49  ...        411             73   
2           0       0        0        0  ...         81             45   
3           0       0        0        0  ...        116             45   
4           0       0        0        0  ...         18             15   
...       ...     ...      ...      ...  ...        ...            ...   
6431        0       0        0        0  ...         47             20   
6432        0       0        0        0  ...         46             18   
6433        0       0        0        0  ...         11              7   
6434        0       0        0        0  ...         45             22   
6435        0       0        0        0  ...         51             19   

      samplingTime_UFP  visits_UFP  uniqueDays_UFP      Neighborhood  \
0                 2340          95              28  Downtown Oakland   
1                 7779         346              53  Downtown Oakland   
2                  724          71              35  Downtown Oakland   
3                  841          63              28  Downtown Oakland   
4                  339          14              13  Downtown Oakland   
...                ...         ...             ...               ...   
6431              2322          57              24          Millbrae   
6432              2284          60              21          Millbrae   
6433               201          19              13          Millbrae   
6434              4520          55              25          Millbrae   
6435              1517          68              24          Millbrae   

          BLOCKID          lat           lon  \
0     60014011003  +37.8249710  -122.2656150   
1     60014011003  +37.8238070  -122.2637676   
2     60014011003  +37.8241874  -122.2658233   
3     60014011003  +37.8236448  -122.2646514   
4     60014013001  +37.8222391  -122.2610172   
...           ...          ...           ...   
6431  60816054005  +37.5883669  -122.3620688   
6432  60816135012  +37.5891595  -122.4128988   
6433  60816135012  +37.5838488  -122.4075351   
6434  60816135012  +37.5819543  -122.4051142   
6435  60816135012  +37.5867238  -122.4102754   

                                               geometry  
0     POLYGON ((-2260969.962 350913.262, -2261011.75...  
1     POLYGON ((-2260735.425 350660.809, -2260737.19...  
2     POLYGON ((-2261011.753 350833.663, -2261038.20...  
3     POLYGON ((-2260863.794 350639.898, -2260903.75...  
4     POLYGON ((-2260690.230 350529.046, -2260672.78...  
...                                                 ...  
6431  POLYGON ((-2276239.619 327700.370, -2276255.16...  
6432  POLYGON ((-2280574.915 328968.419, -2280581.87...  
6433  POLYGON ((-2280244.157 328311.733, -2280280.90...  
6434  POLYGON ((-2280117.647 327862.971, -2280149.01...  
6435  POLYGON ((-2280491.630 328758.534, -2280483.20...  

[6436 rows x 32 c

In [8]:
# How many observations did we lose?
print('Before merge: ',gsw_df.shape[0])
print('After merge: ', gsw_df_merged.shape[0])

Before merge:  6436
After merge:  6436


In [10]:
ejs = pd.read_csv("gis_data/EJSCREEN_2017_USPR_Public.csv")
ejs_ca = ejs[ejs['ID'].astype(str).str.startswith('6')] # ID Column for California starts with a '6'.
ejs_ca['BLOCKID'] = ejs_ca['ID']
ejs_ca.head()

OBJECTID           ID  ACSTOTPOP  ACSIPOVBAS  ACSEDUCBAS  ACSTOTHH  \
10297     10298  60014001001       2952        2952        2420      1286   
10298     10299  60014002001       1071        1071         838       451   
10299     10300  60014002002        913         913         773       381   
10300     10301  60014003001       1414        1414         998       487   
10301     10302  60014003002       1259        1225        1094       701   

       ACSTOTHU  MINORPOP  MINORPCT  LOWINCOME  ...  T_OZONE_D2  \
10297      1374       866  0.293360        225  ...      13%ile   
10298       456       307  0.286648         76  ...      40%ile   
10299       409       231  0.253012        147  ...      46%ile   
10300       530       563  0.398161        122  ...      44%ile   
10301       701       489  0.388403        152  ...      47%ile   

                    T_PM25  T_PM25_D2   AREALAND  AREAWATER  NPL_CNT  \
10297  11.2 ug/m3 (91%ile)      5%ile  6894340.0        0.0        0   
10298  11.3 ug/m3 (92%ile)     28%ile   288960.0        0.0        0   
10299  11.3 ug/m3 (92%ile)     37%ile   298490.0        0.0        0   
10300  11.3 ug/m3 (92%ile)     33%ile   265695.0        0.0        0   
10301  11.3 ug/m3 (92%ile)     39%ile   269098.0        0.0        0   

       TSDF_CNT  Shape_Length    Shape_Area      BLOCKID  
10297         0  18116.601501  1.108122e+07  60014001001  
10298         0   3775.322995  4.642223e+05  60014002001  
10299         0   4019.010837  4.794874e+05  60014002002  
10300         0   3231.259100  4.267776e+05  60014003001  
10301         0   4476.579815  4.321739e+05  60014003002  

[5 rows x 148 columns]

In [11]:
gswej_df = gsw_df_merged.merge(ejs_ca, on='BLOCKID')
gswej_df.head()

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0           1  G06000104011003013           0        0        0         0   
1           2  G06000104011003017         162       60       32         0   
2           3  G06000104011003018           4        0        4         0   
3           4  G06000104011003019           0        0        0         0   
4        1768  G06000104011003006           0        0        0         0   

   AsianNH  PacIsl  OtherNH  HispLat  ...           T_OZONE  T_OZONE_D2  \
0        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
1       20       1        0       49  ...  30.2 ppb (0%ile)      65%ile   
2        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
3        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
4        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   

                T_PM25  T_PM25_D2  AREALAND  AREAWATER  NPL_CNT  TSDF_CNT  \
0  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
1  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
2  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
3  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
4  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   

   Shape_Length     Shape_Area  
0   2471.074533  331230.547284  
1   2471.074533  331230.547284  
2   2471.074533  331230.547284  
3   2471.074533  331230.547284  
4   2471.074533  331230.547284  

[5 rows x 179 columns]

In [12]:
# How many observations did we lose?
print('Before merge: ',gsw_df_merged.shape[0])
print('After merge: ', gswej_df.shape[0])

Before merge:  6436
After merge:  6436


In [13]:
# Convert final df back to GeoDataFrame
geo_df = gpd.GeoDataFrame(gswej_df, geometry = 'geometry')
geo_df.head()

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0           1  G06000104011003013           0        0        0         0   
1           2  G06000104011003017         162       60       32         0   
2           3  G06000104011003018           4        0        4         0   
3           4  G06000104011003019           0        0        0         0   
4        1768  G06000104011003006           0        0        0         0   

   AsianNH  PacIsl  OtherNH  HispLat  ...           T_OZONE  T_OZONE_D2  \
0        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
1       20       1        0       49  ...  30.2 ppb (0%ile)      65%ile   
2        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
3        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
4        0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   

                T_PM25  T_PM25_D2  AREALAND  AREAWATER  NPL_CNT  TSDF_CNT  \
0  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
1  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
2  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
3  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   
4  11.3 ug/m3 (92%ile)     68%ile  206318.0        0.0        0         0   

   Shape_Length     Shape_Area  
0   2471.074533  331230.547284  
1   2471.074533  331230.547284  
2   2471.074533  331230.547284  
3   2471.074533  331230.547284  
4   2471.074533  331230.547284  

[5 rows x 179 columns]

In [16]:
geo_df

Unnamed: 0             GISJOIN  TotalPop.x  WhiteNH  BlackNH  NativeNH  \
0              1  G06000104011003013           0        0        0         0   
1              2  G06000104011003017         162       60       32         0   
2              3  G06000104011003018           4        0        4         0   
3              4  G06000104011003019           0        0        0         0   
4           1768  G06000104011003006           0        0        0         0   
...          ...                 ...         ...      ...      ...       ...   
6431        6432  G06008106054005013           0        0        0         0   
6432        6433  G06008106135012005           0        0        0         0   
6433        6434  G06008106135012012           0        0        0         0   
6434        6435  G06008106135012014           0        0        0         0   
6435        6436  G06008106135012015           0        0        0         0   

      AsianNH  PacIsl  OtherNH  HispLat  ...           T_OZONE  T_OZONE_D2  \
0           0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
1          20       1        0       49  ...  30.2 ppb (0%ile)      65%ile   
2           0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
3           0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
4           0       0        0        0  ...  30.2 ppb (0%ile)      65%ile   
...       ...     ...      ...      ...  ...               ...         ...   
6431        0       0        0        0  ...  30.3 ppb (1%ile)      63%ile   
6432        0       0        0        0  ...  31.6 ppb (2%ile)      48%ile   
6433        0       0        0        0  ...  31.6 ppb (2%ile)      48%ile   
6434        0       0        0        0  ...  31.6 ppb (2%ile)      48%ile   
6435        0       0        0        0  ...  31.6 ppb (2%ile)      48%ile   

                   T_PM25  T_PM25_D2    AREALAND  AREAWATER  NPL_CNT  \
0     11.3 ug/m3 (92%ile)     68%ile    206318.0        0.0        0   
1     11.3 ug/m3 (92%ile)     68%ile    206318.0        0.0        0   
2     11.3 ug/m3 (92%ile)     68%ile    206318.0        0.0        0   
3     11.3 ug/m3 (92%ile)     68%ile    206318.0        0.0        0   
4     11.3 ug/m3 (92%ile)     68%ile    206318.0        0.0        0   
...                   ...        ...         ...        ...      ...   
6431  10.3 ug/m3 (79%ile)     65%ile   1410352.0  1270706.0        0   
6432  9.46 ug/m3 (53%ile)     43%ile  82879623.0  4855266.0        0   
6433  9.46 ug/m3 (53%ile)     43%ile  82879623.0  4855266.0        0   
6434  9.46 ug/m3 (53%ile)     43%ile  82879623.0  4855266.0        0   
6435  9.46 ug/m3 (53%ile)     43%ile  82879623.0  4855266.0        0   

      TSDF_CNT  Shape_Length    Shape_Area  
0            0   2471.074533  3.312305e+05  
1            0   2471.074533  3.312305e+05  
2            0   2471.074533  3.312305e+05  
3            0   2471.074533  3.312305e+05  
4            0   2471.074533  3.312305e+05  
...        ...           ...           ...  
6431         0   9874.143906  4.277380e+06  
6432         0  67988.481817  1.397697e+08  
6433         0  67988.481817  1.397697e+08  
6434         0  67988.481817  1.397697e+08  
6435         0  67988.481817  1.397697e+08  

[6436 rows x 179 columns]

In [14]:
# This cell saves the processed data to a separate folder.
geo_df.to_csv('processed_data/geo_df.csv')

In [15]:
# This cell maps our data coverage.
m = folium.Map([37.8272, 122.2913], zoom_start=5, tiles='cartodbpositron')
folium.GeoJson(geo_df.geometry).add_to(m)
folium.LatLngPopup().add_to(m)
m

In [27]:
only_geo = geo_df.geometry
only_geo.to_csv('processed_data/geometry.csv')